In [1]:
import pandas as pd
import numpy as np
from sklearn.neighbors import NearestNeighbors
from scipy.spatial.distance import euclidean

In [2]:
df = pd.read_csv("onehr.csv")

In [3]:
df

date  WSR0  WSR1  WSR2  WSR3  WSR4  WSR5  WSR6  WSR7  WSR8  ...  \
0       1/1/1998   0.8   1.8   2.4   2.1   2.0   2.1   1.5   1.7   1.9  ...   
1       1/2/1998   2.8   3.2   3.3   2.7   3.3   3.2   2.9   2.8   3.1  ...   
2       1/3/1998   2.9   2.8   2.6   2.1   2.2   2.5   2.5   2.7   2.2  ...   
3       1/4/1998   4.7   3.8   3.7   3.8   2.9   3.1   2.8   2.5   2.4  ...   
4       1/5/1998   2.6   2.1   1.6   1.4   0.9   1.5   1.2   1.4   1.3  ...   
...          ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
2531  12/27/2004   0.3   0.4   0.5   0.5   0.2   0.3   0.4   0.4   1.3  ...   
2532  12/28/2004   1.0   1.4   1.1   1.7   1.5   1.7   1.8   1.5   2.1  ...   
2533  12/29/2004   0.8   0.8   1.2   0.9   0.4   0.6   0.8   1.1   1.5  ...   
2534  12/30/2004   1.3   0.9   1.5   1.2   1.6   1.8   1.1   1.0   1.9  ...   
2535  12/31/2004   1.5   1.3   1.8   1.4   1.2   1.7   1.6   1.4   1.6  ...   

      RH50    U50    V50    HT50     KI     TT      SLP  SLP_  Precp  Class  
0     0.15  10.67  -1.56  5795.0 -12.10  17.90  10330.0 -55.0   0.00      0  
1     0.48   8.39   3.84  5805.0  14.05  29.00  10275.0 -55.0   0.00      0  
2     0.60   6.94   9.80  5790.0  17.90  41.30  10235.0 -40.0   0.00      0  
3     0.49   8.73  10.54  5775.0  31.15  51.70  10195.0 -40.0   2.08      0  
4      NaN    NaN    NaN     NaN    NaN    NaN      NaN   NaN   0.58      0  
...    ...    ...    ...     ...    ...    ...      ...   ...    ...    ...  
2531  0.07   7.93  -4.41  5800.0 -25.60  21.80  10295.0  65.0   0.00      0  
2532  0.04   5.95  -1.14  5845.0 -19.40  19.10  10310.0  15.0   0.00      0  
2533  0.06   7.80  -0.64  5845.0  -9.60  35.20  10275.0 -35.0   0.00      0  
2534  0.25   7.72  -0.89  5845.0 -19.60  34.20  10245.0 -30.0   0.05      0  
2535  0.54  13.07   9.15  5820.0   1.95  39.35  10220.0 -25.0   0.00      0  

[2536 rows x 74 columns]

In [4]:
df.dtypes

date      object
WSR0     float64
WSR1     float64
WSR2     float64
WSR3     float64
          ...   
TT       float64
SLP      float64
SLP_     float64
Precp    float64
Class      int64
Length: 74, dtype: object

In [5]:
df.drop('date', axis=1, inplace=True)

In [6]:
df.isnull().sum()

WSR0     299
WSR1     292
WSR2     294
WSR3     292
WSR4     293
        ... 
TT       125
SLP       95
SLP_     159
Precp      2
Class      0
Length: 73, dtype: int64

In [7]:
df.isnull().sum().sum()

14938

In [8]:
null_counts = df.isnull().sum()
null_percentages = 100 * null_counts / len(df)
null_percentages

WSR0     11.790221
WSR1     11.514196
WSR2     11.593060
WSR3     11.514196
WSR4     11.553628
           ...    
TT        4.929022
SLP       3.746057
SLP_      6.269716
Precp     0.078864
Class     0.000000
Length: 73, dtype: float64

In [9]:
null_counts = df.isnull().sum().sum()
total = df.size
null_percentages = 100 * null_counts / total
print("total nilai :",total)
print("nilai hilang :",null_counts)
print("persentase :",null_percentages)

total nilai : 185128
nilai hilang : 14938
persentase : 8.0690117108163


In [10]:
def jarak(df2,col):
    euc_dist[col] = []
    euc_dist_append =euc_dist[col].append
    for row in range(df2.shape[0]):
        current = df2.index[df2.iloc[:,col] == 0].tolist()
        current = current[0]
        a = df2.iloc[current,col+1:].tolist()
        b = df2.iloc[current,:col].tolist()
        x1 = b+a
        if(row is not current):
            a=df2.iloc[row,col+1:].tolist()
            b=df2.iloc[row,:col].tolist()
            x2=b+a
        else:
            continue
        dist = euclidean(x1,x2)
        euc_dist_append([dist,df2.iloc[row,col]])
#         print(" x1 = ",x1,"\n x2 = ",x2,"\n distance = ",euc_dist[col])

    lst = list(euc_dist[col])
    lst.sort()
    euc_dist[col] = lst
#     print(euc_dist[col])

In [11]:
from collections import Counter

def hitung(val, k, temp=None, i=0, counter=0):
    counts = Counter(val)
    total_count = len(counts)
#     print("jumlah val:", total_count)
    if counter >= int((k/2)+1) and total_count <= 2 :
        print("median : ",int((k/2)+1))
        return temp
    elif i is not k:
        if temp is None:
            temp = val[i]
        elif temp != val[i]:
            temp = val[i]
            counter = 0
        # print(f"temp = {temp} , counter = {counter} , i = {i} , k = {k} , median = {int((k/2)+1)}, val[i] = {val[i]}")
        return hitung(val,k,temp,i+1,counter+1)
    else:
        return None    

def Final(df,col,k):
    terdekat = []
    mean = 0
    minimum = None
    maximum = None
    fuzzy_val = []
    euc_val = []
    terdekat_append = terdekat.append
    fuzzy_append = fuzzy_val.append
    
    for val in range(k):
        terdekat_append(euc_dist[col][val])
    
    for x,y in terdekat:
        if (minimum is None or maximum is None):
            minimum = y
            maximum = y
        elif(y<minimum):
            minimum = y
        elif(y>maximum):
            maximum = y
        mean += y
        euc_val.append(y)
    mean /= len(terdekat)
    euc_val.sort()
    print(euc_val)
    
    fuzzy = hitung(euc_val,7)
    print("min : ",minimum)
    print("max : ",maximum)
    print("mean : ",mean)
    for x,y in terdekat:
        if fuzzy is None:
            fuzzy_append((y,fuzzy_triangular(y,minimum,mean,maximum)))
        else:
            fuzzy_val.append((y,fuzzy))
        
    print("fuzzy : ",fuzzy_val)
    print("fuzzy : ",fuzzy)
    
    pembilang = 0
    penyebut = 0 
    
    for nilai,bobot in fuzzy_val:
        pembilang += nilai*bobot
        penyebut += bobot
            
    print("pembilang : ", pembilang)
    print("penyebut : ",penyebut)
    
    if fuzzy is not None:
        tertimbang = fuzzy
    else:
        tertimbang = pembilang / penyebut
    
    print("rata-rata tertimbang : ",tertimbang)
    index = dummy.index[dummy.iloc[:,col] == 0].tolist()
    index = index[0]
    
    if tertimbang == 0 and index == 0:
        tertimbang = dummy.iloc[index+1, col]
    elif tertimbang == 0:
        tertimbang = dummy.iloc[index-1, col]
            
    dummy.iloc[index,col] = tertimbang
    print(" ")

In [12]:
def fuzzy_triangular(val, minimum, mean, maximum):
   if val <= minimum or val >= maximum: 
        return 0.0
   elif minimum < val <= mean:
        return float((val - minimum)/(mean - minimum)) 
   elif mean < val < maximum:
        return float((maximum - val)/(maximum - mean))

In [13]:
data = df.iloc[:, :-1]
df2 = data.copy()
dummy = df2.fillna(0)
dummy

WSR0  WSR1  WSR2  WSR3  WSR4  WSR5  WSR6  WSR7  WSR8  WSR9  ...   T50  \
0      0.8   1.8   2.4   2.1   2.0   2.1   1.5   1.7   1.9   2.3  ... -15.5   
1      2.8   3.2   3.3   2.7   3.3   3.2   2.9   2.8   3.1   3.4  ... -14.5   
2      2.9   2.8   2.6   2.1   2.2   2.5   2.5   2.7   2.2   2.5  ... -15.9   
3      4.7   3.8   3.7   3.8   2.9   3.1   2.8   2.5   2.4   3.1  ... -16.8   
4      2.6   2.1   1.6   1.4   0.9   1.5   1.2   1.4   1.3   1.4  ...   0.0   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
2531   0.3   0.4   0.5   0.5   0.2   0.3   0.4   0.4   1.3   2.2  ... -12.4   
2532   1.0   1.4   1.1   1.7   1.5   1.7   1.8   1.5   2.1   2.4  ... -12.0   
2533   0.8   0.8   1.2   0.9   0.4   0.6   0.8   1.1   1.5   1.5  ... -11.8   
2534   1.3   0.9   1.5   1.2   1.6   1.8   1.1   1.0   1.9   2.0  ... -10.8   
2535   1.5   1.3   1.8   1.4   1.2   1.7   1.6   1.4   1.6   3.0  ... -11.9   

      RH50    U50    V50    HT50     KI     TT      SLP  SLP_  Precp  
0     0.15  10.67  -1.56  5795.0 -12.10  17.90  10330.0 -55.0   0.00  
1     0.48   8.39   3.84  5805.0  14.05  29.00  10275.0 -55.0   0.00  
2     0.60   6.94   9.80  5790.0  17.90  41.30  10235.0 -40.0   0.00  
3     0.49   8.73  10.54  5775.0  31.15  51.70  10195.0 -40.0   2.08  
4     0.00   0.00   0.00     0.0   0.00   0.00      0.0   0.0   0.58  
...    ...    ...    ...     ...    ...    ...      ...   ...    ...  
2531  0.07   7.93  -4.41  5800.0 -25.60  21.80  10295.0  65.0   0.00  
2532  0.04   5.95  -1.14  5845.0 -19.40  19.10  10310.0  15.0   0.00  
2533  0.06   7.80  -0.64  5845.0  -9.60  35.20  10275.0 -35.0   0.00  
2534  0.25   7.72  -0.89  5845.0 -19.60  34.20  10245.0 -30.0   0.05  
2535  0.54  13.07   9.15  5820.0   1.95  39.35  10220.0 -25.0   0.00  

[2536 rows x 72 columns]

In [14]:
count_zeros = np.count_nonzero(dummy == 0)

print("Jumlah angka 0 dalam dataset:", count_zeros)

Jumlah angka 0 dalam dataset: 17215


In [15]:
euc_dist = {}

In [16]:
for i in range(df2.shape[1]):
    print("Kolom :",i+1)
    current = dummy.index[dummy.iloc[:,i] == 0].tolist()
    for x in current:
        jarak(dummy,i)
        Final(dummy,i,7)
dummy

Kolom : 1
[0.3, 0.4, 0.4, 1.0, 1.1, 1.1, 2.1]
min :  0.3
max :  2.1
mean :  0.9142857142857143
fuzzy :  [(1.1, 0.8433734939759034), (0.4, 0.16279069767441864), (1.1, 0.8433734939759034), (0.4, 0.16279069767441864), (1.0, 0.9277108433734939), (2.1, 0.0), (0.3, 0.0)]
fuzzy :  None
pembilang :  2.9133650882600164
penyebut :  2.940039226674138
rata-rata tertimbang :  0.990927284856571
 
[0.0, 0.0, 0.3, 0.4, 1.0, 3.8, 4.6]
min :  0.0
max :  4.6
mean :  1.442857142857143
fuzzy :  [(0.0, 0.0), (0.4, 0.2772277227722772), (4.6, 0.0), (1.0, 0.693069306930693), (3.8, 0.25339366515837103), (0.3, 0.20792079207920788), (0.0, 0.0)]
fuzzy :  None
pembilang :  1.8292325612651763
penyebut :  1.4316114869405492
rata-rata tertimbang :  1.2777437020810516
 
[0.3, 0.3, 0.4, 0.4, 0.5, 1.0, 1.2]
min :  0.3
max :  1.2
mean :  0.5857142857142857
fuzzy :  [(0.5, 0.7), (0.4, 0.3500000000000001), (0.3, 0.0), (1.0, 0.3255813953488372), (1.2, 0.0), (0.4, 0.3500000000000001), (0.3, 0.0)]
fuzzy :  None
pembilang :  0.

[0.0, 0.1, 0.3, 0.8622350080928095, 0.9, 1.1, 1.5]
min :  0.0
max :  1.5
mean :  0.6803192868704013
fuzzy :  [(0.0, 0.0), (1.5, 0.0), (0.1, 0.1469898060071457), (0.9, 0.7319923360269851), (0.8622350080928095, 0.7780651437706261), (1.1, 0.4879948906846567), (0.3, 0.4409694180214371)]
fuzzy :  None
pembilang :  2.0134522937203534
penyebut :  2.5860115945108504
rata-rata tertimbang :  0.778593683800247
 
[0.0, 0.0, 0.0, 0.1, 0.2, 2.0, 2.4]
min :  0.0
max :  2.4
mean :  0.6714285714285715
fuzzy :  [(0.0, 0.0), (0.2, 0.2978723404255319), (2.0, 0.23140495867768593), (0.0, 0.0), (0.1, 0.14893617021276595), (2.4, 0.0), (0.0, 0.0)]
fuzzy :  None
pembilang :  0.5372780024617548
penyebut :  0.6782134693159838
rata-rata tertimbang :  0.7921960072595281
 
[0.0, 0.2, 0.5, 0.6, 1.3, 2.5, 2.8]
min :  0.0
max :  2.8
mean :  1.1285714285714286
fuzzy :  [(0.0, 0.0), (0.2, 0.17721518987341772), (0.6, 0.5316455696202531), (2.5, 0.1794871794871794), (2.8, 0.0), (1.3, 0.8974358974358974), (0.5, 0.44303797468

[0.0, 0.4, 0.8, 0.8, 0.9, 1.0, 1.6]
min :  0.0
max :  1.6
mean :  0.7857142857142858
fuzzy :  [(0.0, 0.0), (0.8, 0.9824561403508772), (1.0, 0.736842105263158), (1.6, 0.0), (0.9, 0.8596491228070177), (0.4, 0.509090909090909), (0.8, 0.9824561403508772)]
fuzzy :  None
pembilang :  3.2860925039872413
penyebut :  4.0704944178628395
rata-rata tertimbang :  0.8072956664838179
 
[0.0, 0.38187134502923975, 0.6, 0.7, 0.8495750708215295, 1.1, 1.5]
min :  0.0
max :  1.5
mean :  0.733063773692967
fuzzy :  [(0.0, 0.0), (0.38187134502923975, 0.5209251346652698), (1.5, 0.0), (0.7, 0.9548964566528759), (0.8495750708215295, 0.8480821571180827), (0.6, 0.8184826771310365), (1.1, 0.5215557516771481)]
fuzzy :  None
pembilang :  2.652664293310733
penyebut :  3.6639421772444134
rata-rata tertimbang :  0.7239918549439979
 
[0.0, 0.2, 0.6, 1.2, 1.2, 1.3, 1.4]
min :  0.0
max :  1.4
mean :  0.8428571428571427
fuzzy :  [(0.0, 0.0), (1.2, 0.35897435897435886), (1.3, 0.17948717948717924), (1.4, 0.0), (1.2, 0.3589743

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.4]
median :  4
min :  0.0
max :  2.4
mean :  0.34285714285714286
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (2.4, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.4]
median :  4
min :  0.0
max :  2.4
mean :  0.34285714285714286
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (2.4, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 2.4, 2.4, 2.4]
median :  4
min :  0.0
max :  2.4
mean :  1.0285714285714285
fuzzy :  [(0.0, 0.0), (2.4, 0.0), (2.4, 0.0), (2.4, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 2.4, 2.4, 2.4]
median :  4
min :  0.0
max :  2.4
mean :  1.0285714285714285
fuzzy :  [(0.0, 0.0), (2.4, 0.0), (2.4, 0.0), (0.0, 0.0), (2.4, 0.0), (0.0, 0.0), (0.0, 0.0)]
fuzzy 

[0.0, 2.4, 2.4, 2.4, 2.4, 2.4, 2.4]
median :  4
min :  0.0
max :  2.4
mean :  2.0571428571428574
fuzzy :  [(0.0, 2.4), (2.4, 2.4), (2.4, 2.4), (2.4, 2.4), (2.4, 2.4), (2.4, 2.4), (2.4, 2.4)]
fuzzy :  2.4
pembilang :  34.559999999999995
penyebut :  16.8
rata-rata tertimbang :  2.4
 
[0.0, 0.0, 2.4, 2.4, 2.4, 2.4, 2.4]
median :  4
min :  0.0
max :  2.4
mean :  1.7142857142857142
fuzzy :  [(0.0, 2.4), (2.4, 2.4), (2.4, 2.4), (2.4, 2.4), (2.4, 2.4), (0.0, 2.4), (2.4, 2.4)]
fuzzy :  2.4
pembilang :  28.799999999999997
penyebut :  16.8
rata-rata tertimbang :  2.4
 
[0.0, 0.0, 0.0, 0.0, 2.4, 2.4, 2.4]
median :  4
min :  0.0
max :  2.4
mean :  1.0285714285714285
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (2.4, 0.0), (0.0, 0.0), (2.4, 0.0), (2.4, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.4]
median :  4
min :  0.0
max :  2.4
mean :  0.34285714285714286
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0),

...

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0

[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0, 0.0)]
fuzzy :  0.0
pembilang :  0.0
penyebut :  0.0
rata-rata tertimbang :  0.0
 
[0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.57]
median :  4
min :  0.0
max :  1.57
mean :  0.22428571428571428
fuzzy :  [(0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (0.0, 0.0), (1.57, 0.0), (0.0

WSR0  WSR1  WSR2  WSR3  WSR4  WSR5  WSR6  WSR7  WSR8  WSR9  ...   T50  \
0      0.8   1.8   2.4   2.1   2.0   2.1   1.5   1.7   1.9   2.3  ... -15.5   
1      2.8   3.2   3.3   2.7   3.3   3.2   2.9   2.8   3.1   3.4  ... -14.5   
2      2.9   2.8   2.6   2.1   2.2   2.5   2.5   2.7   2.2   2.5  ... -15.9   
3      4.7   3.8   3.7   3.8   2.9   3.1   2.8   2.5   2.4   3.1  ... -16.8   
4      2.6   2.1   1.6   1.4   0.9   1.5   1.2   1.4   1.3   1.4  ... -16.8   
...    ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   ...   
2531   0.3   0.4   0.5   0.5   0.2   0.3   0.4   0.4   1.3   2.2  ... -12.4   
2532   1.0   1.4   1.1   1.7   1.5   1.7   1.8   1.5   2.1   2.4  ... -12.0   
2533   0.8   0.8   1.2   0.9   0.4   0.6   0.8   1.1   1.5   1.5  ... -11.8   
2534   1.3   0.9   1.5   1.2   1.6   1.8   1.1   1.0   1.9   2.0  ... -10.8   
2535   1.5   1.3   1.8   1.4   1.2   1.7   1.6   1.4   1.6   3.0  ... -11.9   

      RH50    U50    V50    HT50     KI     TT      SLP  SLP_  Precp  
0     0.15  10.67  -1.56  5795.0 -12.10  17.90  10330.0 -55.0   0.00  
1     0.48   8.39   3.84  5805.0  14.05  29.00  10275.0 -55.0   0.00  
2     0.60   6.94   9.80  5790.0  17.90  41.30  10235.0 -40.0   0.00  
3     0.49   8.73  10.54  5775.0  31.15  51.70  10195.0 -40.0   2.08  
4     0.49   8.73  10.54  5775.0  31.15  51.70  10192.0 -15.0   0.58  
...    ...    ...    ...     ...    ...    ...      ...   ...    ...  
2531  0.07   7.93  -4.41  5800.0 -25.60  21.80  10295.0  65.0   0.00  
2532  0.04   5.95  -1.14  5845.0 -19.40  19.10  10310.0  15.0   0.00  
2533  0.06   7.80  -0.64  5845.0  -9.60  35.20  10275.0 -35.0   0.00  
2534  0.25   7.72  -0.89  5845.0 -19.60  34.20  10245.0 -30.0   0.05  
2535  0.54  13.07   9.15  5820.0   1.95  39.35  10220.0 -25.0   0.00  

[2536 rows x 72 columns]

In [17]:
dummy.describe()

WSR0         WSR1         WSR2         WSR3         WSR4  \
count  2536.000000  2536.000000  2536.000000  2536.000000  2536.000000   
mean      1.665484     1.625768     1.565333     1.506062     1.500138   
std       1.218724     1.222298     1.182949     1.147198     1.143807   
min       0.100000     0.100000     0.100000     0.100000     0.100000   
25%       0.700000     0.700000     0.700000     0.633251     0.681024   
50%       1.400000     1.300000     1.300000     1.200000     1.200000   
75%       2.400000     2.500000     2.100000     2.100000     2.100000   
max       7.500000     7.700000     7.100000     7.300000     7.200000   

              WSR5         WSR6         WSR7         WSR8         WSR9  ...  \
count  2536.000000  2536.000000  2536.000000  2536.000000  2536.000000  ...   
mean      1.517100     1.617054     2.052968     2.530353     2.871959  ...   
std       1.116931     1.105263     1.115215     1.137994     1.180789  ...   
min       0.100000     0.100000     0.100000     0.100000     0.100000  ...   
25%       0.700000     0.800000     1.242349     1.700000     2.032426  ...   
50%       1.200000     1.300000     1.900000     2.500000     2.800000  ...   
75%       2.100000     2.100000     2.604167     3.200000     3.800000  ...   
max       7.400000     7.400000     7.500000     9.200000     8.500000  ...   

               T50         RH50          U50          V50         HT50  \
count  2536.000000  2536.000000  2536.000000  2536.000000  2536.000000   
mean    -10.415254     0.300899     9.973122     0.809273  5818.297162   
std       3.884836     0.247078     9.407736     7.178934    78.938004   
min     -24.800000     0.010000   -14.920000   -25.990000  5480.000000   
25%     -13.200000     0.090000     2.727500    -3.532500  5770.000000   
50%     -10.000000     0.220000     9.350000     0.360000  5835.000000   
75%      -7.200000     0.470000    16.743049     4.665773  5880.000000   
max      -1.700000     1.000000    42.360000    30.420000  5965.000000   

                KI           TT           SLP         SLP_        Precp  
count  2536.000000  2536.000000   2536.000000  2536.000000  2536.000000  
mean     10.223158    37.152732  10163.862808    -0.019803     0.371439  
std      20.549935    11.205750     52.035130    35.073497     1.317001  
min     -56.700000   -10.100000   9975.000000  -135.000000     0.000000  
25%      -3.725000    31.487500  10130.000000   -20.000000     0.000000  
50%      14.250000    40.800000  10160.000000    -3.060660     0.000000  
75%      27.812500    45.000000  10192.000000    15.000000     0.050000  
max      42.050000    59.150000  10350.000000   140.000000    20.650000  

[8 rows x 72 columns]

# Klasifikasi

In [18]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
from sklearn.tree import DecisionTreeClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.neural_network import MLPClassifier
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score

In [19]:
x = dummy.values
y = df.iloc[:, -1].values

In [25]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.25, random_state=0)

In [26]:
scaler = MinMaxScaler()
x_train = scaler.fit_transform(x_train)
x_test = scaler.transform(x_test)

In [27]:
classifier = DecisionTreeClassifier(max_depth=3)
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

[[613   2]
 [ 17   2]]
0.9700315457413249


In [30]:
classifier = GaussianNB()
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

[[422 193]
 [  5  14]]
0.6876971608832808


In [29]:
classifier = MLPClassifier(hidden_layer_sizes=3, learning_rate_init=0.1, max_iter=100)
classifier.fit(x_train, y_train)
y_pred = classifier.predict(x_test)
cm = confusion_matrix(y_test, y_pred)
accuracy = accuracy_score(y_test, y_pred)
print(cm)
print(accuracy)

[[615   0]
 [ 19   0]]
0.9700315457413249
